# 💻 W08 Lab: SQL Basics: From SELECT to JOIN

**DS105A W08 LAB – Data for Data Science (Autumn Term 2025/2026)**

## 📋 Before You Start

Make sure you have:

- ✅ Attended yesterday's 🖥️ **W08 Lecture** on databases and SQL
- ✅ Completed the 💻 **W07 Lab** (you'll see how SQL achieves the same results as pandas)
- ✅ SQLite Viewer extension installed in VS Code (optional but helpful)

## ⚙️ Library Imports

In [ ]:
import pandas as pd
import sqlite3
import seaborn as sns
import matplotlib.pyplot as plt

%matplotlib inline
%config InlineBackend.figure_formats = ['svg']
sns.set_theme(style="whitegrid", context="talk")

## Part 1: Database Schema Exploration (15 min)

Before writing SQL queries, we need to connect to the database and understand its structure.

### Step 1: Connect to the Database

SQLite databases are stored as files on your computer. We use `sqlite3.connect()` to create a connection object that lets us interact with the database. The connection object (`conn`) is what we pass to `pd.read_sql()` to execute queries.

In [ ]:
# Connect to the pre-built database
conn = sqlite3.connect('./data/opensanctions.db')

### Step 2: Load Tables into Pandas

Before exploring with SQL, let's load all tables into pandas DataFrames. This shows students that `pd.read_sql()` can load entire tables, and gives us DataFrames to compare against SQL results later.

In [ ]:
# Load all tables into pandas DataFrames
df_targets = pd.read_sql("SELECT * FROM targets", con=conn, parse_dates=['first_seen', 'last_seen'])

df_targets_aliases = pd.read_sql("SELECT * FROM target_aliases", con=conn)

df_sanctions = pd.read_sql("SELECT * FROM sanctions", con=conn, parse_dates=['start_date', 'end_date'])

**Explore the database structure using the SQLite Viewer extension in VS Code:**

- Right-click `./data/opensanctions.db` in the file explorer
- Select "Open Database" (if SQLite Viewer extension is installed)
- Browse tables, columns, and relationships visually

### Step 3: Examine Table Schemas with PRAGMA

`PRAGMA table_info()` is a [SQLite-specific command](https://sqlite.org/pragma.html) that returns information about a table's structure. It shows column names, data types, whether columns can be NULL, default values, and which column is the primary key (`pk` column: 1 = primary key, 0 = not).

In [ ]:
# Examine targets table structure
query = """
PRAGMA table_info(targets)
"""
pd.read_sql(query, conn)

In [ ]:
# Examine sanctions table structure
query = """
PRAGMA table_info(sanctions)
"""
pd.read_sql(query, conn)

In [ ]:
# Examine target_aliases table structure
query = """
PRAGMA table_info(target_aliases)
"""
pd.read_sql(query, conn)

### Step 4: Reflection Questions

**Answer in a markdown cell:**

1. Why do you think companies separate data into multiple tables instead of a single large one?
2. Identify the primary keys and foreign keys in these tables.
3. To count sanctioning countries, which table(s) would you need?

**Your answers:**

## Part 2: Progressive SQL Skill Building (50 min)

Build SQL skills step by step. Each task adds one new concept to your toolkit. After each SQL query, we show the pandas equivalent using the DataFrames we loaded in Part 1, so you can see how both approaches achieve the same result.

<div style="font-family: system-ui; padding: 15px 20px; background-color: #fcfcfc; color: #212121; border-left: 6px solid #e53e3e; border-radius: 4px; margin: 1.5em 0; box-shadow: 0 2px 4px rgba(0,0,0,0.1);max-width:600px">

<strong style="font-size: 1.1em;">⚠️ PAY CLOSE ATTENTION</strong><br/>

As you work through these SQL skills, notice when the syntax feels intuitive versus when it feels confusing. SQL reads like English in many places (SELECT, WHERE, FROM), but some parts require careful thinking (GROUP BY, COUNT DISTINCT).<br/>


<strong>Ask your class teacher immediately when something doesn't click.</strong> Don't simply get something out of AI and rush to Part 3. Understand what you're doing!

</div>

### Skill 1: SELECT Columns (5 min)

**Task:** Get the first 5 targets with their `target_id`, `caption`, `country`, `first_seen`, and `last_seen` columns.

In [ ]:
# Task: Get first 5 targets with selected columns
query = """
SELECT 
    target_id,
    caption,
    country,
    first_seen,
    last_seen
FROM targets 
LIMIT 5
"""

pd.read_sql(query, conn, parse_dates=['first_seen', 'last_seen'])

💭 **THINK ABOUT IT:** Do you see the point of `LIMIT` here?

💪 **Pandas version:**

How would you achieve the same result using `df_targets`?

### Skill 2: WHERE Filtering (8 min)

**Task:** Show all sanctions for which we know the status (where `status` IS NOT NULL).

In [ ]:
# Task: Show all sanctions with known status
query = """
SELECT 
    sanction_id,
    target_id,
    country,
    status,
    start_date,
    end_date
FROM sanctions 
WHERE status IS NOT NULL
"""

pd.read_sql(query, conn)

💪 **Pandas version:**

Exercise your pandas skills and get the same result using `df_sanctions`:

### Skill 3: COUNT Aggregation (8 min)

**Task:** Count how many rows exist for which we DON'T KNOW the status (where `status` IS NULL).

In [ ]:
# Task: Count sanctions with unknown status
query = """
SELECT 
    COUNT(*) as count
FROM sanctions
WHERE status IS NULL
"""

pd.read_sql(query, conn)

💪 **Pandas version:**

### Skill 4: COUNT DISTINCT (8 min)

**Task:** Count how many unique countries appear in the `sanctions` table (excluding NULL values).

In [ ]:
# Task: Count unique countries in sanctions
query = """
SELECT 
    COUNT(DISTINCT country) as num_countries
FROM sanctions
WHERE country IS NOT NULL
"""

pd.read_sql(query, conn)

💪 **Pandas version:**

<div style="font-family: system-ui; padding: 15px 20px; background-color: #fcfcfc; color: #212121; border-left: 6px solid #e53e3e; border-radius: 4px; margin: 1.5em 0; box-shadow: 0 2px 4px rgba(0,0,0,0.1);max-width:600px">

<strong style="font-size: 1.1em;">⚠️ CRITICAL SKILL</strong><br/>


GROUP BY is the most important concept for Part 3. Watch carefully how it splits data into categories and applies COUNT to each group.<br/>



Compare the SQL result with your pandas translation. Do they match? If not, which one is wrong?

</div>

### Skill 5: GROUP BY (10 min)

**Task:** Count how many sanctions exist per status type.

In [ ]:
# Task: Count sanctions per status
query = """
SELECT 
    status,
    COUNT(*) as count
FROM sanctions
GROUP BY status
ORDER BY count DESC
"""

pd.read_sql(query, conn)

💭 **THINK ABOUT IT:** 

* Do you get why we have the `*` in the `COUNT(*)`? (Ask your class teacher if you're unsure)

* Do you understand the point of `ORDER BY` and `DESC` here? What do you think are the equivalents in pandas?

💪 **Pandas version:**

<div style="font-family: system-ui; padding: 15px 20px; background-color: #fcfcfc; color: #212121; border-left: 6px solid #e53e3e; border-radius: 4px; margin: 1.5em 0; box-shadow: 0 2px 4px rgba(0,0,0,0.1);max-width:600px">

<strong style="font-size: 1.1em;">⚠️ CONNECTING TABLES</strong><br/>

JOINs connect tables using common columns. The pattern is:<br/>

<code>LEFT JOIN table2 ON table1.key = table2.key</code><br/>

This skill connects to yesterday's lecture. 

</div>

### Skill 6: JOIN Tables (10 min)

**Task:** Join the `sanctions` table with the `targets` table to show sanction information alongside target captions.

SQL JOINs combine data from multiple tables using a common key. Here we use `target_id` to connect sanctions to their targets.

In [ ]:
# Task: Join sanctions with targets to get target captions
query = """
SELECT 
    *
FROM sanctions AS s
LEFT JOIN targets AS t ON s.target_id = t.target_id
"""

pd.read_sql(query, conn)

💭 **THINK ABOUT IT:** Which columns come from the `sanctions` table and which come from the `targets` table?

Now look at a more complex example, where beyond the `JOIN` we also filter the results and limit the number of rows returned.

In [ ]:
# Task: Join sanctions with targets to get target captions
query = """
SELECT 
    s.sanction_id,
    s.country,
    s.status,
    s.start_date,
    t.target_id,
    t.caption
FROM sanctions AS s
LEFT JOIN targets AS t
    ON s.target_id = t.target_id
WHERE s.status IS NOT NULL
LIMIT 10
"""

pd.read_sql(query, conn)

💪 **Pandas version:**

(Replicate the previous SQL query using pandas)

## Part 3: Creating plot_df and Visualization (15 min)

Now that you've learned the SQL building blocks, let's combine them to recreate the `plot_df` from W07 Lab and create a visualization.

### Step 1: Create plot_df with SQL

**Task:** Recreate the `plot_df` from W07 Lab using SQL. Show the top 10 countries by unique target count.

<details style="background-color: #fcfcfc;border: 1px solid #e0e0e0;border-left: 5px solid #333;border-radius: 0.25rem;padding: 0.5em 0.5em 0.5em 1em;margin-bottom: 1em;overflow: hidden;font-size: 0.85em;">
<summary>💪 Click HERE to see the pandas version</summary>

The code below is not exactly the same as the previous week but only because the `sanctions` table is slightly different.

```python
plot_df_pandas = (
    df_sanctions[df_sanctions['country'].notna()]
    .groupby('country')
    .agg(num_targets=('target_id', 'nunique'))
    .sort_values('num_targets', ascending=False)
    .reset_index()
    .head(10)
)
```

</details>

This combines all skills: SELECT, WHERE, COUNT DISTINCT, GROUP BY, ORDER BY, LIMIT.

In [ ]:
# Task: Top 10 countries by UNIQUE target count (recreate W07 plot_df)
# Combine all skills you learned: SELECT, WHERE, COUNT DISTINCT, GROUP BY, ORDER BY, LIMIT
query = """

"""

plot_df = pd.read_sql(query, conn)
plot_df

📋 **JUST SO YOU KNOW:** Data analysts frequently write queries like the above and save them to a `.sql` file so they can re-run them frequently and monitor changes in the data (for example, to check sales revenue over time per category).

### Step 2: Recreate the Bar Chart

Reuse the seaborn plotting code from W07 Lab to visualise your `plot_df`:

In [ ]:
# Create bar chart from plot_df
plt.figure(figsize=(9, 6))
sns.barplot(
    data=plot_df,
    x='num_targets',
    y='country',
    color='#b2182b'
)
plt.title(
    'The US and Ukraine are the most active sanctioning authorities\nin our sample of Russian targets',
    fontsize=16, loc='left'
)
plt.xlabel('Number of targets')
plt.ylabel('Sanction country (ISO code)')
plt.tight_layout()
plt.show()

### Step 3: Reflection Questions

🗣️ **CLASSROOM DISCUSSION**

Your class teacher will mediate a discussion on the following questions. Feel free to add your own answers to a Markdown cell below this one.

1. SQLite is optional for Mini-Project 2. Would it help your project? Why or why not?
2. TfL data has nested journeys/legs. If using SQLite, what tables would you create?
3. When would you choose SQL over pandas? When would you choose pandas over SQL?

**Your answers:**

---

## ✅ Lab Complete

You've successfully learned SQL basics by querying a real database. You can now:

- Write SELECT queries with filtering
- Aggregate data with COUNT and GROUP BY
- Sort and limit results
- Create visualizations from SQL query results

**Next steps:**

- Optional: Explore `W08-NB03-Lab-Building-Database.ipynb` to see how this database was built
- Apply SQL skills to Mini-Project 2 if you choose to use SQLite
- Attend office hours if you need help with json_normalize for MP2

In [ ]:
# Close database connection
conn.close()